In [ ]:
from yahoofinancials import YahooFinancials as yf
import numpy as np
import matplotlib.pyplot as plt
import random
random.seed(0)
np.random.seed(1)

In [ ]:
chars = ['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z']

In [ ]:
def getCounts(date1, date2):    
    counts = {"With": 0, "Out performed": 0, "Under performed": 0}
    yfSPY = yf(['SPY'])
    spyData = yfSPY.get_historical_price_data(date1, date2, 'daily')
    spyReturn = (spyData['SPY']['prices'][-1]['close'] - spyData['SPY']['prices'][0]['close']) / spyData['SPY']['prices'][0]['close'] 
    
    while sum(counts.values()) <  35:
        ticker = ""
        ticker += chars[random.randint(0, 25)]
        ticker += chars[random.randint(0, 25)]
        ticker += chars[random.randint(0, 25)]
        try:
            yfTicker = yf([ticker])
            tickerData = yfTicker.get_historical_price_data(date1, date2, 'daily')
            if tickerData.values() == [None]:
                continue
            tickerReturn = (tickerData[ticker]['prices'][-1]['close'] - tickerData[ticker]['prices'][0]['close']) / tickerData[ticker]['prices'][0]['close'] 
        except:
            continue
        if abs(spyReturn - tickerReturn) < .08:
            counts["With"] += 1
        elif tickerReturn - spyReturn > 0:
            counts["Out performed"] += 1
        else:
            counts["Under performed"] += 1
    
    return counts
counts = getCounts('2022-11-01', '2023-11-01')

In [ ]:
withProb = counts['With'] / sum(counts.values())
overProb = counts['Out performed'] / sum(counts.values())
underProb = counts['Under performed'] / sum(counts.values())

In [ ]:
print(withProb, overProb, underProb)

In [ ]:
#Citation: Some code adapted from EPS 109 homework/lab
%matplotlib qt
from matplotlib.animation import FFMpegWriter
fig = plt.figure(dpi=250)
metadata = dict(title='Stock', artist='Matplotlib',comment='Simulation')
writer = FFMpegWriter(fps=7, metadata=metadata,bitrate=200000)
with writer.saving(fig, "animation.mp4", dpi=250):
    chart = np.zeros((200, 200))
    chart[:,0] = 1
    prev_y = 8
    for i in range(0,10000):
        x  = np.random.randint(0,200)
        y  = prev_y
        while True:
            num = np.random.random()
            x_0 = x
            y_0 = y
            if 0 <= num < underProb - .01:
                x -= 1
                if x < 0:
                    x = 199
                    
            if underProb - .01 <= num < underProb + overProb - .01:
                x += 1
                if x >= 200:
                    x = 0
                
            if underProb + overProb - .01 <= num:
                y -= 1
            
            if y > prev_y or chart[x][y] == 1: 
                x = x_0
                y = y_0
                continue
                
            b = False
            for xNew in [x-1,x+1]:
                if xNew < 0 or xNew >= 200:
                    continue
                if chart[xNew][y] == 1:
                    chart[x][y] = 1
                    if y > prev_y - 7 and y < 193: 
                        prev_y = y + 7

                    if i % 200 == 0: 
                        plt.imshow(chart, cmap='Greens') 
                        plt.axis('off')
                        plt.show()
                        plt.draw()
                        plt.pause(0.01)
                        writer.grab_frame()
                    b = True
                    break
                
            if b:
                break
            
            for yNew in [y-1,y+1]:
                if yNew < 0 or yNew >= 200:
                    continue
                    
                if chart[x][yNew] == 1:
                    chart[x][y] = 1
                    if y > prev_y - 7 and y < 193: 
                        prev_y = y + 7

                    if i % 200 == 0: 
                        plt.imshow(chart, cmap='Greens') 
                        plt.axis('off')
                        plt.show()
                        plt.draw()
                        plt.pause(0.01)
                        writer.grab_frame()
                    b = True
                    break
            if b:
                break
                
        if y + 1 == 200: 
            break